In [16]:
import pandas as pd
import matplotlib.pyplot as plt
import joblib
from functions.functions import fill_num,fill_cat
from sklearn.preprocessing import StandardScaler, FunctionTransformer
from sklearn.compose import ColumnTransformer






In [23]:
# Load the reference and production dataframes
df_reference = pd.read_csv("../application_train.csv")
df_production = pd.read_csv("../application_test.csv")

In [24]:
    num_cols=df_reference.select_dtypes(exclude=["object"]).columns.tolist()
    num_cols=[col for col in num_cols if col!="TARGET"]
    cat_cols=df_reference.select_dtypes(include=["object"]).columns.tolist()

    num_imputer=FunctionTransformer(func=fill_num)
    cat_imputer=FunctionTransformer(func=fill_cat)

    imputer=ColumnTransformer(
        transformers=[("num",num_imputer,num_cols),
        ("cat",cat_imputer,cat_cols)]
    )

In [25]:



    df_reference_filled = imputer.fit_transform(df_reference)
    df_reference_filled = pd.DataFrame(df_reference, columns=num_cols + cat_cols)


In [26]:
    df_production_filled = imputer.transform(df_production)
    df_production_filled = pd.DataFrame(df_production_filled, columns=num_cols + cat_cols)

In [27]:
model = joblib.load('./models/logreg_model.joblib')


In [28]:
df_production["TARGET"]=model.predict(df_production_filled)

In [31]:
from evidently.report import Report
from evidently.metric_preset import DataDriftPreset

report = Report(metrics=[
    DataDriftPreset(), 
])

report.run(reference_data=df_reference, current_data=df_production)
report.show(mode='inline')

C:\Users\hugo\anaconda3\lib\site-packages\umap\distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
C:\Users\hugo\anaconda3\lib\site-packages\umap\distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
C:\Users\hugo\anaconda3\lib\site-packages\umap\distances.py:1086: NumbaDeprecationWarning: The 'nopython' keyword 


#### Mesures à prendre lorsqu'il y a un data drift :

<b>Analyser la cause du data drift</b> : Identifiez les raisons potentielles du drift en examinant les modifications dans les données de production par rapport aux données de référence.
Cela peut inclure des changements dans la distribution des valeurs, des valeurs aberrantes, des valeurs manquantes, etc.

<b> Vérifier les pipelines de prétraitement </b> : Assurez-vous que les pipelines de prétraitement des données sont cohérents entre les données de référence et les données de production. Si des différences sont observées, il peut être nécessaire d'ajuster les étapes de prétraitement pour traiter les changements dans les données.

<b>Réévaluer les caractéristiques (features)</b> : Revoyez les caractéristiques utilisées pour l'entraînement du modèle et vérifiez si elles sont toujours pertinentes et représentatives des données de production. Vous pouvez avoir besoin de réexaminer les caractéristiques existantes ou d'ajouter de nouvelles caractéristiques pour capturer les changements dans les données.

<b> Réentraîner le modèle </b> : Si le data drift est significatif et affecte les performances du modèle, envisagez de réentraîner le modèle en utilisant les données de production mises à jour. Cela permettra au modèle de s'adapter aux nouvelles conditions des données.

<b> Mettre en place un système de surveillance continu </b>: Établissez un système de surveillance continu pour détecter les variations dans les données en temps réel. Cela peut inclure la surveillance des statistiques descriptives, des indicateurs de performance du modèle ou l'utilisation de méthodes de détection de changement de données.

<b>Effectuer une validation régulière </b>: Planifiez des évaluations régulières du modèle en utilisant des données de validation ou de test pour vérifier si les performances du modèle sont maintenues au fil du temps malgré le data drift. Si nécessaire, ajustez les hyperparamètres ou effectuez d'autres modifications pour améliorer les performances du modèle.

 <b>Documenter et communiquer</b> : Documentez les observations de data drift, les mesures prises et les décisions prises pour permettre une meilleure compréhension et une communication claire avec les parties prenantes concernées.

En adoptant une approche proactive pour gérer le data drift, vous pourrez maintenir la performance et la fiabilité de votre modèle dans des environnements de données changeants.